In [64]:
import scrapy
import requests
from scrapy.http import TextResponse
import pandas as pd

In [ ]:
# 1. Start project

In [42]:
!scrapy startproject daangn

Error: scrapy.cfg already exists in /Users/fofx/dss15/crawling_project/daangn


In [3]:
# 2. items.py

In [ ]:
# %load daangn/daangn/items.py

In [74]:
%%writefile daangn/daangn/items.py
# '''
# region = 거래지역; ~구~ 동까지 표기됨
# temperature = 거래 온도; 좋은 거래를 할수록 온도가 높아짐
# chat_counts = 판매자와 구매 관심자의 채팅이 오고 간 횟수
# watch_counts = 찜한 횟수
# '''
import scrapy


class DaangnItem(scrapy.Item):
    title = scrapy.Field() 
    user_id = scrapy.Field()
    temperature = scrapy.Field()
    region = scrapy.Field() 
    price = scrapy.Field() 
    link = scrapy.Field()
    desc = scrapy.Field() 
    chat_counts = scrapy.Field() 
    watch_counts = scrapy.Field() 
    view_counts = scrapy.Field()
    

Overwriting daangn/daangn/items.py


In [ ]:
# 3. spider.py

In [75]:
%%writefile daangn/daangn/spiders/spider.py
import string
import scrapy
from scrapy import Request
from daangn.items import DaangnItem

class DaangnSpider(scrapy.Spider):
    name = 'Daangn'
    start_urls = ["https://www.daangn.com/search/macbook/more/flea_market?page=1"]
    page_number = 2
    
    def parse(self, response):
        xp = "/html/body/article/a/@href"
        urls = response.xpath(xp).extract()
        # get full url
        urls =  list(map(response.urljoin, urls))
        return (Request(url, callback=self.parse_content) for url in urls)
    
    def parse_content(self, response):
        item = DaangnItem()
        item['title'] = response.xpath('//*[@id="article-title"]/text()')[0].extract().strip()
        item['price'] = response.xpath('//*[@id="article-price"]/text()')[0].extract().strip()
        desc = response.xpath('//*[@id="article-detail"]/p/text()').extract()
        item['desc'] = "".join(desc).replace('\n', '')
        item['user_id'] = response.xpath('//*[@id="nickname"]/text()')[0].extract().strip()
        item['temperature'] = response.xpath('//*[@id="temperature-wrap"]/dd/text()')[0].extract().strip()
        item['link'] = response.xpath('/html/head/link[1]/@href')[0].extract()
        item['region'] = response.xpath('//*[@id="region-name"]/text()')[0].extract().strip()
        counts = response.xpath('//*[@id="article-counts"]/text()')[0].extract().strip()
        item['chat_counts'] = counts.split('∙')[0].strip().split(' ')[1]
        item['watch_counts'] = counts.split('∙')[1].strip().split(' ')[1]
        item['view_counts'] = counts.split('∙')[2].strip().split(' ')[1]
       
        yield item
        
        next_page = 'https://www.daangn.com/search/macbook/more/flea_market?page=' + str(DaangnSpider.page_number)
        if DaangnSpider.page_number <= 800:
            DaangnSpider.page_number += 1
            yield response.follow(next_page, callback = self.parse)

Overwriting daangn/daangn/spiders/spider.py


In [76]:
%%writefile run.sh
cd daangn
rm items.csv
scrapy crawl Daangn -o items.csv

Overwriting run.sh


In [77]:
%%time
!/bin/bash run.sh

2020-11-24 15:03:27 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: daangn)
2020-11-24 15:03:27 [scrapy.utils.log] INFO: Versions: lxml 4.5.0.0, libxml2 2.9.9, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.7.6 (default, Jan  8 2020, 13:42:34) - [Clang 4.0.1 (tags/RELEASE_401/final)], pyOpenSSL 19.1.0 (OpenSSL 1.1.1d  10 Sep 2019), cryptography 2.8, Platform Darwin-19.6.0-x86_64-i386-64bit
2020-11-24 15:03:27 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.selectreactor.SelectReactor
2020-11-24 15:03:27 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'daangn',
 'NEWSPIDER_MODULE': 'daangn.spiders',
 'SPIDER_MODULES': ['daangn.spiders']}
2020-11-24 15:03:28 [scrapy.extensions.telnet] INFO: Telnet Password: 41bd174e551cc62f
2020-11-24 15:03:28 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusage.MemoryUsage',
 'scrapy.extensions.feedexpo

2020-11-24 15:03:29 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/151368310>
{'chat_counts': '4',
 'desc': '2020년 2월 6일 구매프로세서 : 2.3GHz 8코어 Intel Core i9메모리 : 16GB 2667MHz '
         'DDR4용량 : 1TB SSD그래픽 : Radeon Pro 5500M 4G키보드 : 한국어애플케어플러스 적용중 (명의이전 '
         '가능)배터리 사이클 8박스 있음들고다닐 용도로 구매했으나, 크기와 무게 때문에 거의 사용하지 않은 상태입니다.가볍고 작은 '
         '13인치 구매하려구요..맥북 본체에 스크래치하나 없고, 충전 어댑터에는 약간의 스크래치 있습니다.',
 'link': 'https://www.daangn.com/articles/151368310',
 'price': '3,000,000원',
 'region': '구로구 구로제3동',
 'temperature': '38.1',
 'title': '맥북 프로 16인치 2019 고급형(MacBook Pro 16-inch, 2019, MVVK2KH/A)',
 'user_id': '루나픽시',
 'view_counts': '643',
 'watch_counts': '11'}
2020-11-24 15:03:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/articles/146403990> (referer: https://www.daangn.com/search/macbook/more/flea_market?page=1)
2020-11-24 15:03:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/search/macbook/more/flea_marke

2020-11-24 15:03:30 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/153937121>
{'chat_counts': '1',
 'desc': '1) 외관/액정/키보드/백라이트/음량/와이파이/블루투스/기타 기능들 모두 정상입니다. 사진 첨부합니다. 2. 새로운 '
         'macOS Big sur 업데이트 완료했습니다. 3. 사양은 기본i3에서 한 단계 업그레이드된 중급 i5입니다. '
         '4.원하시는 사진, 사양, 상태 전부 인증가능합니다. 전자 제품이라서 직거래로만 거래합니다. 만나서 차분하게 살펴 보시고 '
         '결정하셔도 됩니다. 배터리 싸이클이 16입니다. 웹서핑 정도만 했고 저한테 과분한 노트북인거 같아서 판매합니다. 5. '
         '박스랑 충전기선, 충전기 어댑터 모두 있습니다. 직거래 쿨거래 하시면 MacBook Air 전용 파우치를 드리고 '
         '20,000원 네고도 해드립니다. ',
 'link': 'https://www.daangn.com/articles/153937121',
 'price': '1,050,000원',
 'region': '종로구 연지동',
 'temperature': '37.0',
 'title': '맥북에어(MacBook Air) 2020 / 중급형(i5) / A급 / 배터리 사이클 16회 판매합니다',
 'user_id': '연지동직거래',
 'view_counts': '84',
 'watch_counts': '4'}
2020-11-24 15:03:30 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/148186544>
{'chat_counts': '0',
 'desc': '1) MacBook Pro(15-inch, Early 2011)- 제품 잘 작동되고 상태(

2020-11-24 15:03:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/articles/128120507> (referer: https://www.daangn.com/search/macbook/more/flea_market?page=10)
2020-11-24 15:03:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/search/macbook/more/flea_market?page=15> (referer: https://www.daangn.com/articles/105361243)
2020-11-24 15:03:30 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/search/macbook/more/flea_market?page=14> (referer: https://www.daangn.com/articles/145820171)
2020-11-24 15:03:30 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/151714127>
{'chat_counts': '2',
 'desc': '2015 맥북프로 레티나 13인치 256GB입니다.어도비 프로그램 다 잘 돌아고 잘 '
         '사용했는데(포토샵,일러스트,프리미어,에펙,시포디,다빈치)16인치로 바꾸면서 기존 13인치 맥북 팝니다.하드케이스+커버 '
         '케이스 항상 착용하고 다녀서흠집 거의 없고 사진에 나온 정도의 흠집 및케이스 자국이 살짝 남아있습니다.액정보호필름 및 '
         '키보드 보호필름 착용돼있어서그 부분은 아주 깨끗합니다.충전기는 피복 벗겨짐이 있어서 하얀색 절연테이프로 잘 붙여놓았고 '
         '충전은 잘됩니다.팔기전에 

2020-11-24 15:03:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/search/macbook/more/flea_market?page=33> (referer: https://www.daangn.com/articles/153360585)
2020-11-24 15:03:31 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/articles/108609793> (referer: https://www.daangn.com/search/macbook/more/flea_market?page=19)
2020-11-24 15:03:31 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/148535118>
{'chat_counts': '8',
 'desc': '애플 공홈에서 구입했고 9월 2일날 배송 도착 후 넷플릭스나 웹서핑용으로만 사용했는데 급하게 돈 필요해서 판매합니당맥북에어 '
         '2020 13인치 스페이스그레이 쿼드코어 i3/ 램8/ ssd 256기가 완전 기본형이에용주로 이불 위에서만 사용해서 '
         '기스나 하자 일절 없습니당 뒷판이나 옆판 보고싶으시면 당근톡으로 보내드려용 ',
 'link': 'https://www.daangn.com/articles/148535118',
 'price': '960,000원',
 'region': '남구 삼산동',
 'temperature': '37.5',
 'title': '맥북에어 2020 기본형 팔아용',
 'user_id': 'alterlove',
 'view_counts': '1065',
 'watch_counts': '25'}
2020-11-24 15:03:31 [scrapy.core.engine] DEBUG: Crawled (200) <

...

2020-11-24 15:08:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/150200882>
{'chat_counts': '1',
 'desc': '맥북프로레티나 2013 early 13인치 판매합니다.430,000원 입니다.사진에 컴퓨터 세부사항 포함했으니 '
         '확인부탁드리고 추가적인 사항은 채팅주세요.(SSD 256GB)직거래 선호하며 평일 서울 강남, 한남 주말 수원 영통 '
         '가능합니다.(택배도 가능합니다)구성은 본체와 사용감 많은 맥세이프2 60w 입니다.',
 'link': 'https://www.daangn.com/articles/150200882',
 'price': '430,000원',
 'region': '수원시 영통구 영통1동',
 'temperature': '36.8',
 'title': '맥북프로레티나 13인치 (2013 early), MACBOOK PRO RETINA',
 'user_id': '삼삼오오',
 'view_counts': '838',
 'watch_counts': '17'}
2020-11-24 15:08:47 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/articles/154324656> (referer: https://www.daangn.com/search/macbook/more/flea_market?page=7)
2020-11-24 15:08:47 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/articles/154333676> (referer: https://www.daangn.com/search/macbook/more/flea_market?page=7)
2020-11-24 15:08:47 [scrapy.core.engine] 

2020-11-24 15:08:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/150937538>
{'chat_counts': '4',
 'desc': '맥북에어 기본형 스페이스그레이 팝니다 7월 구매 후 집에서만 사용했고유튜브 넷플릭스 시청위주로 사용했습니다사이클회수는 '
         '18회입니다사진에 있는 가방, 키스킨 같이 드립니다 겉면에 보호필름도 붙여져있는데 불편하시면 제거하시면 됩니다 이제 사용할 '
         '일이 없어 팝니다완전 깨끗하게 사용했습니다 하자 하나도 없는 거의 새상품입니다직거래위치는 경남 창원, 김해, 인근지역 '
         '가능합니다 부산도 가능합니다 연락주세요\u200b1.1GHz 듀얼 코어 10세대 Intel Core i3프로세서(최대 '
         '3.2GHz Turbo Boost)Intel Iris Plus Graphics8GB 3733MHz LPDDR4X '
         '메모리256GB SSD 저장 장치¹',
 'link': 'https://www.daangn.com/articles/150937538',
 'price': '1,000,000원',
 'region': '창원시 성산구 내동',
 'temperature': '37.3',
 'title': '맥북 에어 2020 (Macbook air 2020)',
 'user_id': '허뚜뚜',
 'view_counts': '578',
 'watch_counts': '11'}
2020-11-24 15:08:47 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/articles/135411210> (referer: https://www.daangn.com/search/macbook/more/flea_market?page=4)
2020-11-24 15:08:47 [scrapy.c

2020-11-24 15:08:48 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/articles/147350915> (referer: https://www.daangn.com/search/macbook/more/flea_market?page=4)
2020-11-24 15:08:48 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/152856616>
{'chat_counts': '0',
 'desc': '애플 맥북에어 2020 Macbook Air 레티나 디스플레이 13인치 기본형스페이스그레이 거의 새것, 사이클 수 7, '
         '실사용 10번 미만구매시기 10월 중순원래 쓰는 맥북 프로 서브로 구매했는데 생각만큼 자주 안쓰게 되어 내놓습니다.',
 'link': 'https://www.daangn.com/articles/152856616',
 'price': '1,100,000원',
 'region': '유성구 궁동',
 'temperature': '36.7',
 'title': '맥북에어 2020 Macbook Air 거의 새것',
 'user_id': 'snow',
 'view_counts': '480',
 'watch_counts': '10'}
2020-11-24 15:08:48 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/articles/150586122> (referer: https://www.daangn.com/search/macbook/more/flea_market?page=4)
2020-11-24 15:08:48 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/articles/153761916> (refere

2020-11-24 15:08:48 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/153541228>
{'chat_counts': '0',
 'desc': '맥북 프로 13인치 판매합니다.1년 전에 맥북 프로 15인치 사면서 팔까 했는데 사과에 불 들어오는 모델이기도 하고 혹시 '
         '몰라서 그냥 안 팔았는데 역시 사용을 안 하게 되네요.. 중급형으로 256gb이고, cto 제품으로 cpu i5 '
         '2.9ghz에 램 16gb입니다.그리고 구입 시기 2016년 6월입니다.중급형에 cpu랑 램 둘 다 업그레이드한 cto '
         '제품이라 기본 모델 보다 훨씬 비싸게 주고 샀습니다. 램 업그레이드만 해도 20만원은 더 비쌌으니까요.그리고 cto '
         '제품이라 중고 제품도 잘 없을 겁니다.외관은 사진에서처럼 위에는 기스 전혀 없고, 아래판은 오른쪽 상단 쪽에 살짝 파인 '
         '부분이랑 가운데 스크레치 조금 있습니다. 그 외에 화면에 부분적으로 코팅 벗겨짐이 있습니다만 화면 꺼진 상태에서 불빛에 '
         '비춰야 보이는 정도고 화면 켜진 상태에서는 전혀 안 보입니다. 배터리는 작년 9월에 애플스토어에서 새로 교체했습니다. '
         '그래서 사이클수가 25 밖에 안 됩니다.충전기는 조금 사용감 있지만 작동은 아무 문제 없이 잘됩니다. 관심 있으신 분 연락 '
         '부탁드려요. 그리고 노트북이다 보니 직거래만 희망합니다.',
 'link': 'https://www.daangn.com/articles/153541228',
 'price': '870,000원',
 'region': '중구 다산동',
 'temperature': '36.5',
 'title': 'Macbook Pro (Retina, 13 inch Early 2015) 맥북 프로 MF840KH/A cto',
 '

2020-11-24 15:08:49 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/154157432>
{'chat_counts': '0',
 'desc': '13인치 맥북프로 (모델명: A2159) 실버 팝니다. 스펙은 사진 참고해 주세요. 올해 3월초에 가로수길 애플 '
         '프리스비에서 구매했습니다. 애플케어 (AppleCare+) 2023년 3월 10일까지입니다. 상태 S+ 급입니다. 하자 및 '
         '스크레치 없습니다. 서울 직거래만 합니다. 구입 당시 박스랑 충전기 애플 스티커 그리고 투명 보호 케이스 포함. ',
 'link': 'https://www.daangn.com/articles/154157432',
 'price': '1,790,000원',
 'region': '관악구 신림동',
 'temperature': '37.7',
 'title': '맥북프로 13인치 2019형 256GB 실버 터치바/ MacBook Pro 13 inch',
 'user_id': 'AppleBeats',
 'view_counts': '90',
 'watch_counts': '2'}
2020-11-24 15:08:49 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.daangn.com/search/macbook/more/flea_market?page=13> (referer: https://www.daangn.com/articles/146403990)
2020-11-24 15:08:49 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.daangn.com/articles/151889152>
{'chat_counts': '1',
 'desc': '·',
 'link': 'https://www.daangn.com/articles/151889152

In [78]:
pd.read_csv("/Users/fofx/dss15/crawling_project/daangn/items.csv")

chat_counts                                               desc  \
0               1  맥북에어 2019년 a1932 emc 3184 레티나 13인치 팝니다. 서브용으로 ...   
1               0  맥북 프로 15인치 2013년도 고급형 판매합니다.i7 2.3 쿼드코어입니다.풀박이...   
2               2  맥북프로 15인치 터치바 2017년형입니다2019년에 구입했고 실사용은 몇 달 안된...   
3               0  품명 : 맥북 15인치 hardgraft(하드그래프트) 맥북 슬리브구매시기 : 20...   
4               1  * 256GB* 최근 수리* 포맷완료* 풀박스* 직거래해요* 깨끗하게 쓰시라고 알코...   
...           ...                                                ...   
7536            0  MacBook Air Model A1466 (13-inch, Early 2015)1...   
7537            0  14인치 19년3월제조 19년 10월부터사용했습니다. 화면,위아래 옆  보호필름다해...   
7538            0  14년식이구요15년구매상품입니다사진보시면 보이지않는 눌림약간보이네요사진참고하세요배터...   
7539            2  2018년 11월에 애플 Authorized Reseller에서 구매했고i7 885...   
7540            0  (원주에서 팔 수 있으면 좋을거 같아서 중나 올린가격보다 꽤싸게 올려봅니다. ) 여...   

                                           link       price       region  \
0     https://www.daangn.com/articles/153142981    750,000원  성남시 분당구 분당동   
1     https://www.daangn.com/articles/154263336    850,000원  수원시 영통구 망포동   
2     https://www.daangn.com/articles/150455627  1,500,000원      당진시 채운동   
3     https://www.daangn.com/articles/106983152     40,000원     서초구 서초1동   
4     https://www.daangn.com/articles/151356238    820,000원      성동구 행당동   
...                                         ...         ...          ...   
7536  https://www.daangn.com/articles/154308209    550,000원  성남시 분당구 수내동   
7537  https://www.daangn.com/articles/154240774     11,111원      구미시 구평동   
7538  https://www.daangn.com/articles/151888543    390,000원      서구 월평2동   
7539  https://www.daangn.com/articles/152174521  1,800,000원  용인시 기흥구 마북동   
7540  https://www.daangn.com/articles/154268382  3,600,000원    원주시 반곡관설동   

      temperature                                              title  \
0            65.4           2019년형 맥북(MacBook) 에어 레티나 13인치 노트북 a1932   
1            36.7  Macbook Pro (Retina, 15-inch, Late 2013) 맥북 프로...   
2            37.0      Macbook Pro 15inch 맥북 프로 15인치 2017년 (스페이스그레이)   
3            40.4            [A급상품] 맥북 15인치 hardgraft(하드그래프트) 맥북 슬리브   
4            36.5      맥북프로 Macbook Pro, 13인치 Early 2015 & 애플 매직마우스2   
...           ...                                                ...   
7536         39.0                                맥북에어 13, 8GB, 256GB   
7537         37.3                                  그램으로 맥북에어랑 교환해봅니다   
7538         28.0                                 맥북에어14년식13인치 15년구매   
7539         37.3                        2018 맥북 프로 15인치 고급형 (512GB)   
7540         39.2              2020 맥북프로16인치 고급형 CTO (램/그래픽) 스페이스그레이   

         user_id  view_counts  watch_counts  
0            된장국          349            18  
1            최의현           47             1  
2     windsurfer          134             0  
3          베이삐대디          464             5  
4             채니          456            15  
...          ...          ...           ...  
7536        나무와숲           16             1  
7537         동이래            6             0  
7538          클거          128             2  
7539    yountofu          229             7  
7540          췌북           65             5  

[7541 rows x 10 columns]